# PROJECT 1 
### Author : Sourav Yadav(17285)

To predict the Compound state(inhibition cut-off 75%) i.e. compound is active if inhibition value > 75% otherwise inactive.  


### Our Approach : 

Rather than predicting inhibition values, we chose to classify a compound as active or inactive(inhibition value > 75% are active), mainly because the latter performs considerably better. This comes with a little loss in precision, but nevertheless is a good predictor of what might work and what doesn't work. Also, reduces our working set to a great degree.  





### Data Collection :
 
The Coronaviridae are a family of positive single stranded encapsulated viruses. They typically cause mild respiratory diseases, but infections with the ß-coronavirus SARS-CoV, MERS and SARS-CoV-2 can lead to acute respiratory diseases and high mortality, particularly in individuals with underlying health conditions. In the last 20 years, Coronaviridae have emerged in two severe outbreaks, 2002/2003 with SARS-CoV, 2012 with MERS and one pandemic, in late 2019 with SARS-CoV-2. At the time of writing, the coronavirus SARS-Cov-2 pandemic has led to close to 39 million confirmed infections and 1 million deaths (https://coronavirus.jhu.edu). 

Multiple interventional clinical trials have been initiated in the search for effective pharmacological treatments against SARS-CoV-2 infection and the related disease Covid-19. Bioinformatics analyses have proposed repurposed drugs based on the interactome between viral encoded proteins and host-cell pathways. In the absence of safe and effective vaccines against SARS-CoV-2, repurposing of existing drugs represents a first pragmatic strategy for the treatment of Covid-19 patients. We thus identify potential inhibitors of SARS-CoV-2 in-vitro cellular toxicity in human (Caco-2) cells by predicting its bioactivity using ML after training the data on a large scale drug repurposing collection[3]. Bioactivity describes the characteristic of an implant material to interact with or initiate a specific reaction of living tissue upon exposure. The biochemical systems encountered by a drug molecule (implant material) are extremely complex. The factors affecting the bioactivity[4] may be divided into three categories: 1. Physicochemical properties such as solubility, partition coefficients, and ionization. 2. Chemical structure parameters such as resonance, inductive effect, oxidation potentials, types of bonding, and isosterism. 3. Spatial considerations such as molecular dimensions, interatomic distances, and stereochemistry.

To identify possible candidates for progression towards clinical studies against SARS-CoV-2, the authors of the paper[1] screened a well-defined collection of compounds. We obtained this data via the data base - ChEMBL_27 SARS-CoV-2 release under the title Identification of inhibitors of SARS-CoV-2 in-vitro cellular toxicity in human (Caco-2) cells using a large scale drug repurposing collection[3]. 

We obtain this data in two parts as follows:

1. inhibition.csv – Data in this data set is used for stating the bioactivity measure which are trained against the corresponding attributes from compounds.csv to classify compounds into two categories active and inactive. A compound is called active if it's inhibition value is greater than 75% otherwise it is classified as inactive.  

2. compounds.csv – Data in this data set is used for stating factors that affect towards bioactivities as stated previously. The factors selected from the given set of attributes are Molecular Weight, AlogP, PSA, HBA, HBD, CX ApKa, CX BpKa & CX LogD which we shall use as our descriptors.


### Importing the Libraries 

In [2]:
#Linear Algebra 
import numpy as np 

#Data processing 
import pandas as pd 

#Preprocessing/Model Selection 
from sklearn.model_selection import train_test_split, cross_validate
from pandas_profiling import ProfileReport

#Classifiers
from sklearn.linear_model import LogisticRegression, Perceptron, SGDClassifier
from sklearn.ensemble import RandomForestClassifier
from sklearn.svm import SVC 

### Data Processing

In [3]:
df_compounds = pd.read_csv('compounds.csv', sep=';').drop_duplicates('ChEMBL ID')
df_inhibition = pd.read_csv('inhibition.csv', sep=';').drop_duplicates('Molecule ChEMBL ID')
df = df_compounds.merge(df_inhibition, how='inner', left_on='ChEMBL ID', right_on='Molecule ChEMBL ID', validate='one_to_one')
df = df[['Molecular Weight_x', 'AlogP_x','PSA','HBA', 'HBD','CX ApKa', 'CX BpKa', 'CX LogD','QED Weighted','Standard Value']]
df = df.replace(to_replace='None', value=np.nan).dropna()
df['Bioactivity'] = df.apply(lambda df: df['Standard Value']>75, axis=1).astype(int)
df = df.apply(pd.to_numeric)
df.info()
df.describe(include="all") 

<class 'pandas.core.frame.DataFrame'>
Int64Index: 1909 entries, 0 to 5614
Data columns (total 11 columns):
 #   Column              Non-Null Count  Dtype  
---  ------              --------------  -----  
 0   Molecular Weight_x  1909 non-null   float64
 1   AlogP_x             1909 non-null   float64
 2   PSA                 1909 non-null   float64
 3   HBA                 1909 non-null   int64  
 4   HBD                 1909 non-null   int64  
 5   CX ApKa             1909 non-null   float64
 6   CX BpKa             1909 non-null   float64
 7   CX LogD             1909 non-null   float64
 8   QED Weighted        1909 non-null   float64
 9   Standard Value      1909 non-null   float64
 10  Bioactivity         1909 non-null   int64  
dtypes: float64(8), int64(3)
memory usage: 179.0 KB


Molecular Weight_x      AlogP_x          PSA          HBA          HBD  \
count         1909.000000  1909.000000  1909.000000  1909.000000  1909.000000   
mean           400.865663     2.533133    98.185904     5.684652     2.556836   
std            155.540670     2.443517    50.761157     2.874941     1.801043   
min             75.070000    -8.900000     3.240000     1.000000     0.000000   
25%            297.270000     1.100000    67.160000     4.000000     1.000000   
50%            392.440000     2.800000    88.850000     5.000000     2.000000   
75%            487.410000     4.130000   114.620000     7.000000     3.000000   
max           1385.460000    11.510000   437.280000    25.000000    16.000000   

           CX ApKa      CX BpKa      CX LogD  QED Weighted  Standard Value  \
count  1909.000000  1909.000000  1909.000000   1909.000000     1909.000000   
mean      8.714060     6.160272     0.891964      0.522745       11.122142   
std       4.127851     3.087110     3.365741      0.212746       24.691942   
min      -4.370000     0.000000   -17.920000      0.020000      -39.640000   
25%       4.670000     3.620000    -0.620000      0.370000       -2.650000   
50%       9.810000     6.720000     1.530000      0.520000        2.920000   
75%      12.280000     8.890000     3.050000      0.690000       14.120000   
max      14.000000    15.380000    10.040000      0.940000      135.090000   

       Bioactivity  
count  1909.000000  
mean      0.051336  
std       0.220740  
min       0.000000  
25%       0.000000  
50%       0.000000  
75%       0.000000  
max       1.000000

### Data Analysis 

In [4]:
prof = ProfileReport(df)
prof

Render HTML: 100%|██████████| 1/1 [00:03<00:00,  3.12s/it]


In [5]:
#Active indexes 
active = df[lambda df : df['Standard Value']>75]
active.describe()

Molecular Weight_x    AlogP_x         PSA        HBA        HBD  \
count           98.000000  98.000000   98.000000  98.000000  98.000000   
mean           458.143878   4.071224   91.467347   5.959184   2.132653   
std            130.964269   2.062545   33.450349   2.237996   1.163338   
min            142.160000  -1.320000   23.470000   2.000000   0.000000   
25%            382.197500   2.737500   65.827500   5.000000   1.000000   
50%            459.560000   4.120000   91.970000   6.000000   2.000000   
75%            525.140000   5.420000  111.422500   7.000000   3.000000   
max           1004.840000   9.760000  201.750000  14.000000   6.000000   

         CX ApKa    CX BpKa    CX LogD  QED Weighted  Standard Value  \
count  98.000000  98.000000  98.000000     98.000000       98.000000   
mean   10.201122   5.848571   2.873265      0.481735       92.029286   
std     3.400624   2.737110   2.226608      0.181875       10.763740   
min     0.360000   0.270000  -4.510000      0.110000       75.060000   
25%     8.510000   3.712500   1.467500      0.370000       83.865000   
50%    11.650000   5.810000   3.075000      0.470000       92.500000   
75%    12.652500   8.357500   4.195000      0.607500       99.865000   
max    13.900000  10.830000   9.200000      0.860000      135.090000   

       Bioactivity  
count         98.0  
mean           1.0  
std            0.0  
min            1.0  
25%            1.0  
50%            1.0  
75%            1.0  
max            1.0

### Model 


In [8]:
x = df.drop(['Standard Value', 'Bioactivity', 'QED Weighted'], axis=1)
y = df[['Bioactivity']]
qed = df[['QED Weighted']]

x_train, x_test, y_train, y_test = train_test_split(x, y, test_size=0.2)
model = SVC(kernel='rbf',C=1.0,gamma='scale')
model.fit(x_train, y_train)
cv_results = cross_validate(model, x, y, cv=5, return_train_score=True)
    
print("Training Score {}\n".format(model.score(x_train, y_train)))
print("Testing Score {}\n ".format(model.score(x_test, y_test)))
print("Cross Validation Train Scores: {}\n".format(cv_results['train_score']))
print("Cross Validation Train Mean: {}\n".format(np.mean(cv_results['train_score'])))
print("Cross Validation Test Scores: {}\n".format(cv_results['test_score']))
print("Cross Validation Test Mean: {}\n".format(np.mean(cv_results['test_score'])))

Training Score 0.9482645710543549

Testing Score 0.9502617801047121
 
Cross Validation Train Scores: [0.94826457 0.94891945 0.94891945 0.94891945 0.94829843]

Cross Validation Train Mean: 0.9486642700158061

Cross Validation Test Scores: [0.95026178 0.94764398 0.94764398 0.94764398 0.95013123]

Cross Validation Test Mean: 0.9486649901746574



### References

1. https://www.researchsquare.com/article/rs-23951/v1

2. https://www.ncbi.nlm.nih.gov/pmc/articles/PMC3524573/

3. https://www.ebi.ac.uk/chembl/document_report_card/CHEMBL4303101/

4. https://www.drugtimes.org/how-drugs-act/factors-affecting-bioactivity.html

5. https://www.researchgate.net/figure/Values-MW-clogP-HBA-HBD-PSA-logBB-and-logP-e-a-for-ML-and-1_tbl1_259626002